In [7]:
from pathlib import Path
from network_wrangler.transit import load_transit

EXAMPLE_DIR = Path.cwd().parent / "examples"
STPAUL = EXAMPLE_DIR / "stpaul"
SMALL = EXAMPLE_DIR / "small"
TEST_DATA = Path.cwd().parent / "tests" / "data"

In [26]:
from projectcard import read_card

# Release Overview of Wrangler v1.0

*Compared to pre 1.0*

## Features

1. I/O and Mutation Speed
2. Implicit and fast validation
3. Flexible serialization formats
4. Improved stability
5. Selection flexibility for transit based on any feature or by link or node
6. More flexible and fast transition to geodataframes for (almost) any data part
7. Easy data clipping to geographic bounds
8. Scripts for actions you might want to execute from command line (i.e. data conversion/clipping/etc)
9. Logging
10. Error descriptions


## Tech Overhead Investment

1. Separation of causes prevents circular reference collisions, limits import bloat, and improves legibility/organization.
    - Project card functionality in project card repo
    - Separate modules for separate functionality
2. Reliability achieved through more testable code and expanding test coverage with more test cases and also anti-patterns
    - Testable code
    - Test coverage
3. Explicit data models that make complex data structures obvious and easy to validate
    - Legible
    - Self-documenting
    - Flexible
    - Validatable
4. Clean code principles that make code easier to test and maintain
    - more functions that do a single thing...and do it well
    - classes that are small - functions that access or manipulate them
5. Documentation
    - consistent and detailed functional documentation
    - consistent type hints
    - usage for modules and classes
    - overall documentation leverages the flexible and less bloated MkDocs package
6. Removes less-well-maintained dependencies
    - Replaces Partridge with internal functionality


## Speed

### I/O Speed

1. Makes the heavy shapes.geojson optional and doesn't read it in for operations that don't directly involve it.
2. Leverages `pandera` for speedy, vector-based data model validation for dataframes
3. Replaces row-based calculations for blank geographic values with vector-based calculations
4. Provides flexibility for I/O serialization formats that are faster – like Parquet.

In [13]:
from network_wrangler.roadway import load_roadway_from_dir

STPAUL_ROAD = load_roadway_from_dir(STPAUL)

/Users/elizabeth/opt/miniconda3/envs/wrangler/lib/python3.10/site-packages/geopandas/geoseries.py:645: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  result = super().apply(func, convert_dtype=convert_dtype, args=args, **kwargs)
/Users/elizabeth/opt/miniconda3/envs/wrangler/lib/python3.10/site-packages/geopandas/geoseries.py:645: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  result = super().apply(func, convert_dtype=convert_dtype, args=args, **kwargs)


In [78]:
STPAUL_TRANSIT = load_transit(STPAUL)

/Users/elizabeth/opt/miniconda3/envs/wrangler/lib/python3.10/site-packages/pandera/engines/pandas_engine.py:842: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  col = to_datetime_fn(col, **self.to_datetime_kwargs)
/Users/elizabeth/opt/miniconda3/envs/wrangler/lib/python3.10/site-packages/pandera/engines/pandas_engine.py:842: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  col = to_datetime_fn(col, **self.to_datetime_kwargs)
Table trips for specified FK                                         frequencies.trip_id not in <class 'network_wrangler.transit.feed.Feed'>                                         - skipping validation.
Table agencies for specified FK                                        routes.agency_id not 

In [11]:
STPAUL_TRANSIT.feed.stops

stop_id stop_code  ...                         node_ssid parent_station
0     10037       NaN  ...  98e48a4ff360a8833c1f04b975fb8f73            NaN
1     10039       NaN  ...  1203d85e0764f1e36a8a598977364db0            NaN
2     10040       NaN  ...  3127e296d73928bc1cec808a7acd6d3a            NaN
3     10041       NaN  ...  0c017fc146f71e6b5e8fb8ad17e95fd5            NaN
4     10042       NaN  ...  7d8495c9a972d3a5610639e4765aa0b2            NaN
..      ...       ...  ...                               ...            ...
458    1579    1579.0  ...  c23797607a0dcb04bc511a6dd873c580            NaN
459    1583    1583.0  ...  c23797607a0dcb04bc511a6dd873c580            NaN
460    1611    1611.0  ...  72536d59385b843b0ff608b6a1da58c4            NaN
461    1612    1612.0  ...  72536d59385b843b0ff608b6a1da58c4            NaN
462    1753    1753.0  ...  ba5d8492794497f86393fe71d65dbbeb            NaN

[463 rows x 14 columns]

### Selection Speed

1. Caches selections and references them if network hasn’t changed using hashes so that costly selections that involve connecting a shortest path don't have to be performed again.

In [14]:
sel_dict = {
    "modes": ["walk"],
    "links": {
        "name": ["Valley Street"],
    },
    "from": {"model_node_id": 174762},
    "to": {"model_node_id": 43041},
}
STPAUL_ROAD.get_selection(sel_dict)

In [15]:
# note same physical address
STPAUL_ROAD.get_selection(sel_dict)

In [18]:
STPAUL_ROAD.get_selection(sel_dict).selected_links

[460228, 481940]

In [19]:
STPAUL_ROAD.get_selection(sel_dict).selected_links_df

model_link_id  ...                                           geometry
index                  ...                                                   
460228         460228  ...  LINESTRING (-93.09891 44.95851, -93.09961 44.9...
481940         481940  ...  LINESTRING (-93.09961 44.95857, -93.09971 44.9...

[2 rows x 31 columns]

### Setting roadway net speed

- Will also only re-perform validation and network consistency calculation if either road network or transit network feed has changed.

In [20]:
STPAUL_TRANSIT.road_net = STPAUL_ROAD

In [21]:
STPAUL_TRANSIT.road_net.nodes_df.head()

model_node_id osm_node_id  ...          X          Y
model_node_id_idx                             ...                      
1924                        1924        1924  ... -93.136654  44.969831
1925                        1925        1925  ... -93.137132  44.964678
1930                        1930        1930  ... -93.141544  44.953727
1931                        1931        1931  ... -93.141543  44.957543
1932                        1932        1932  ... -93.141546  44.961179

[5 rows x 13 columns]

### Project Apply Speed

1. Replaced most row-based functions with vector-based functions - new road/managed lane


In [27]:
card_path = STPAUL / "project_cards" / "road.prop_change.managed_lanes.yml"
card = read_card(card_path)
stpaul_roads_w_managed_lanes = STPAUL_ROAD.apply(card)

/Users/elizabeth/opt/miniconda3/envs/wrangler/lib/python3.10/site-packages/geopandas/geoseries.py:645: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  result = super().apply(func, convert_dtype=convert_dtype, args=args, **kwargs)
/Users/elizabeth/Documents/urbanlabs/MetCouncil/working/network_wrangler/network_wrangler/roadway/links.py:657: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[{'default': 0, 'timeofday': [{'timespan': (21600, 32400), 'value': 1}, {'timespan': (54000, 64800), 'value': 1}]}
 {'default': 0, 'timeofday': [{'timespan': (21600, 32400), 'value': 1}, {'timespan': (54000, 64800), 'value': 1}]}
 {'default': 0, 'timeofday': [{'timespan': (21600, 32400), 'value': 1}, {'timespan': (54000, 64800), 'value': 1}]}
 {'default': 0, 'timeofday': [{'timespan': (21600, 3

### Convert to model net

In [29]:
m_net = stpaul_roads_w_managed_lanes.model_net
m_net.m_links_df.head()

model_link_id osm_link_id  ...     GP_A     GP_B
model_link_id_idx                             ...                  
1390239                  1390239              ...  35491.0  87993.0
1390344                  1390344              ...  35754.0  37457.0
1391206                  1391206              ...  38765.0  35491.0
1401484                  1401484              ...  87982.0  35754.0
390239                    390239    35277986  ...      NaN      NaN

[5 rows x 37 columns]

## Implicit and Fast Validation

In [30]:
bad_project_card = r"/Users/elizabeth/Documents/urbanlabs/working/projectcard/tests/data/cards/multiple-highway.bad.yaml"
read_card(bad_project_card)

SubprojectValidationError: Subproject of Multiple Highway                  should only have one change. Did you forget to indent the rest of this change?.

In [5]:
bad_network = load_roadway_from_dir(TEST_DATA / "roadway_input_fail" / "missing_nodes")

/Users/elizabeth/opt/miniconda3/envs/wrangler/lib/python3.10/site-packages/geopandas/geoseries.py:645: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  result = super().apply(func, convert_dtype=convert_dtype, args=args, **kwargs)
/Users/elizabeth/opt/miniconda3/envs/wrangler/lib/python3.10/site-packages/geopandas/geoseries.py:645: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  result = super().apply(func, convert_dtype=convert_dtype, args=args, **kwargs)


ValueError: Missing from/to nodes in nodes_df: [[1 2]
 [2 1]
 [3 1]
 [1 8]
 [8 1]]

In [8]:
bad_transit_network = load_transit(TEST_DATA / "transit_input_fail" / "bad_prop_values")

/Users/elizabeth/opt/miniconda3/envs/wrangler/lib/python3.10/site-packages/pandera/engines/pandas_engine.py:842: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  col = to_datetime_fn(col, **self.to_datetime_kwargs)
/Users/elizabeth/opt/miniconda3/envs/wrangler/lib/python3.10/site-packages/pandera/engines/pandas_engine.py:842: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  col = to_datetime_fn(col, **self.to_datetime_kwargs)
Table trips for specified FK                                         frequencies.trip_id not in <class 'network_wrangler.transit.feed.Feed'>                                         - skipping validation.


SchemaErrors: {
    "DATA": {
        "DATATYPE_COERCION": [
            {
                "schema": "RoutesTable",
                "column": "route_type",
                "check": "coerce_dtype('category')",
                "error": "Error while coercing 'route_type' to type category: Could not coerce <class 'pandas.core.series.Series'> data_container into type category:   index  failure_case0      0          9999"
            }
        ]
    },
    "SCHEMA": {
        "WRONG_DATATYPE": [
            {
                "schema": "RoutesTable",
                "column": "route_type",
                "check": "dtype('category')",
                "error": "expected series 'route_type' to have type category, got int64"
            }
        ]
    }
}

## Serialization Formats

Multiple serialization formats and an API and script to translate.
- Parquet
- Geojson/json
- CSV
- Pickle

Network-reading methods will auto-detect format.

In [ ]:
from network_wrangler.roadway import write_roadway

write_roadway(STPAUL_ROAD, file_format="parquet", out_dir="nothere", overwrite=True)

In [ ]:
from network_wrangler.transit import write_transit

write_transit(STPAUL_TRANSIT, file_format="parquet", out_dir="nothere", overwrite=True)

## Stability

- Handles a lot more cases - has been tested on a lot more cases.
- If fails, should tell you why and what you need to do.


Has 187 tests - most on multiple cases.

## Transit Selection Features

- Select by any trip or route characteristic
- Select by nodes
- One or more timespans

In [ ]:
selection_dict = {
    "route_properties": {"route_long_name": ["Express", "Ltd Stop"]},
    "trip_properties": {"my_awesome_trip_attribute": [1, 2, 3]},
    "nodes": {"model_node_id": [3, 4, 5]},
    "timepans": [["12:00:00", "1:00:00"], ["18:00,00", "19:00:00"]],
}

## GeoDataFrames

- All roadway tables are stored in GeoDataFrames for easy viewing
- Transit is easily transferred to GeoDataFrames

In [35]:
my_net = STPAUL_ROAD.links_df.sample(300).explore(tiles="CartoDB positron")
STPAUL_ROAD.nodes_df.sample(300).explore(m=my_net, color="grey")
my_net

In [36]:
STPAUL_TRANSIT.shapes_gdf.explore(m=my_net, color="limegreen")
STPAUL_TRANSIT.stops_gdf.explore(m=my_net, color="limegreen")
my_net

/Users/elizabeth/Documents/urbanlabs/MetCouncil/working/network_wrangler/network_wrangler/transit/geo.py:121: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  .apply(lambda x: LineString(zip(x[1], x[0])), axis=1)


## Clipping

- Easily clip roadway or transit features using API or script
- Explore more in `Clip Networks.ipynb`

In [46]:
from network_wrangler.roadway import clip_roadway

clipped_road_downtown = clip_roadway(
    STPAUL_ROAD, boundary_geocode="Downtown St. Paul, MN"
)
my_map2 = clipped_road_downtown.links_df.explore(color="grey", tiles="CartoDB positron")

In [47]:
clipped_road_eco = clip_roadway(STPAUL_ROAD, boundary_file=TEST_DATA / "ecolab.geojson")
clipped_road_eco.links_df.explore(m=my_map2, color="hotpink")

In [51]:
from network_wrangler.transit import clip_transit

clipped_transit_eco = clip_transit(STPAUL_TRANSIT, roadway_net=clipped_road_eco)
clipped_transit_eco.shape_links_gdf.explore(m=my_map2, color="turquoise")

Table trips for specified FK                                         frequencies.trip_id not in <class 'network_wrangler.transit.feed.Feed'>                                         - skipping validation.
Table agencies for specified FK                                        routes.agency_id not in table list - skipping validation.
Referencing table trips not yet set in                                        <class 'network_wrangler.transit.feed.Feed'> - skipping fk validation.


## Scripts

#### Wrangler helper scripts

- `clip_transit`
- `clip_roadway`
- `convert_network`

Have fairly good support, documentation and help from command line

In [62]:
! ../bin/clip_transit.py --help

pyogrio not installed, falling back to default engine (fiona)
/Users/elizabeth/opt/miniconda3/envs/wrangler/lib/python3.10/site-packages/pydantic/_internal/_fields.py:151: UserWarning: Field "model_node_id" has conflict with protected namespace "model_".

You may be able to resolve this warning by setting `model_config['protected_namespaces'] = ()`.
  warnings.warn(
agency_id='1' agency_name='Transit Agency' agency_url=Url('https://example.com/') agency_timezone='America/New_York' agency_lang='en' agency_phone='123-456-7890' agency_fare_url=Url('https://example.com/fares') agency_email='info@example.com'
usage: clip_transit.py [options] <network_path> <boundary> <out_dir>

Trim a transit network based on a given boundary.

positional arguments:
  network_path          Path to the input transit network directory.
  boundary              Path to the boundary file (shapefile, geoparquet or
                        GeoJSON) or a geocode representing the boundary.
  out_dir               Pat

#### Project Card Scripts

There are also helper scripts in project card:

- `validate_card`
- `update_project_card_schema`

In [63]:
!validate_card /Users/elizabeth/Documents/urbanlabs/MetCouncil/working/network_wrangler/examples/stpaul/project_cards/road.add.simple.yml

In [64]:
!validate_card /Users/elizabeth/Documents/urbanlabs/working/projectcard/tests/data/cards/transit-property-change.v0.yaml

---- Error validating Blue Line Service Enhancement C ----

Relevant schema: {'$schema': 'http://json-schema.org/draft-07/schema', 'type': 'object', '$defs': {'change_roadway_deletion': {'$schema': 'http://json-schema.org/draft-07/schema#', 'type': 'object', 'anyOf': [{'required': ['links']}, {'required': ['nodes']}], 'examples': [{'links': {'model_link_id': [1, 2, 3]}}, {'links': {'ref': ['I-5'], 'lanes': 2}}, {'nodes': {'model_node_id': [1, 2, 3]}}], 'additionalProperties': False, 'properties': {'links': {'$schema': 'http://json-schema.org/draft-07/schema', 'description': 'requirements for describing links in the `facility` section of a project card.', 'type': 'object', 'title': 'Roadway link selection', 'oneOf': [{'required': ['name']}, {'required': ['ref']}, {'required': ['osm_link_id']}, {'required': ['model_link_id']}, {'required': ['all']}], 'additionalProperties': True, 'not': {'anyOf': [{'required': ['from']}, {'required': ['to']}]}, 'examples': [{'name': ['Main St'], 'modes':

## Code Complexity



### Cyclomatic Complexity

[Radon](https://radon.readthedocs.io/) 

> Cyclomatic Complexity corresponds to the number of decisions a block of code contains plus 1. This number (also called McCabe number) is equal to the number of linearly independent paths through the code. This number can be used as a guide when testing conditional logic in blocks.

Average complexity: B (8.392857142857142)

In [53]:
! radon cc ../network_wrangler --average

../network_wrangler/logger.py
    F 15:0 setup_logging - A
../network_wrangler/scenario.py
    M 389:4 Scenario._check_projects_conflicts - B
    M 414:4 Scenario.order_projects - B
    M 467:4 Scenario._apply_change - B
    M 240:4 Scenario._add_project - B
    M 554:4 Scenario.summarize - B
    C 57:0 Scenario - A
    M 116:4 Scenario.__init__ - A
    M 331:4 Scenario._check_projects_planned - A
    M 343:4 Scenario._check_projects_have_project_cards - A
    M 353:4 Scenario._check_projects_prerequisites - A
    M 371:4 Scenario._check_projects_corequisites - A
    F 607:0 create_base_scenario - A
    M 176:4 Scenario.create_scenario - A
    M 494:4 Scenario._apply_project - A
    M 520:4 Scenario.apply_projects - A
    M 164:4 Scenario.queued_projects - A
    M 171:4 Scenario.__str__ - A
    M 222:4 Scenario._add_dependencies - A
    M 286:4 Scenario.add_project_cards - A
    M 455:4 Scenario.apply_all_projects - A
    C 41:0 ScenarioConflictError - A
    C 45:0 ScenarioCorequisiteE

## Maintainability

### Maintainability Index

[Radon](https://radon.readthedocs.io/) 

> Maintainability Index is a software metric which measures how maintainable (easy to support and change) the source code is. The maintainability index is calculated as a factored formula consisting of SLOC (Source Lines Of Code), Cyclomatic Complexity and Halstead volume.

In [54]:
! radon mi ../network_wrangler -s

../network_wrangler/__init__.py - A (100.00)
../network_wrangler/logger.py - A (94.32)
../network_wrangler/scenario.py - A (44.55)
../network_wrangler/viz.py - A (82.46)
../network_wrangler/utils/geo.py - A (58.68)
../network_wrangler/utils/time.py - A (81.14)
../network_wrangler/utils/models.py - A (77.76)
../network_wrangler/utils/net.py - A (80.43)
../network_wrangler/utils/io.py - A (65.13)
../network_wrangler/utils/__init__.py - A (100.00)
../network_wrangler/utils/utils.py - A (59.54)
../network_wrangler/utils/data.py - A (51.47)
../network_wrangler/models/projects/types.py - A (100.00)
../network_wrangler/models/gtfs/records.py - A (100.00)
../network_wrangler/models/gtfs/__init__.py - A (100.00)
../network_wrangler/models/gtfs/types.py - A (100.00)
../network_wrangler/models/gtfs/tables.py - A (69.79)
../network_wrangler/models/gtfs/gtfs.py - A (97.56)
../network_wrangler/models/gtfs/table_types.py - A (75.26)
../network_wrangler/models/roadway/types.py - A (72.76)
../network_w

## Organization

In [73]:
!tree ../network_wrangler -L 1 -I '.*|*.pyc|__pycache__'

../network_wrangler
├── __init__.py
├── logger.py
├── models
├── roadway
├── scenario.py
├── transit
├── utils
└── viz.py

5 directories, 4 files


In [76]:
!tree ../network_wrangler/roadway -L 2 -I '.*|*.pyc|__pycache__'

../network_wrangler/roadway
├── __init__.py
├── clip.py
├── convert.py
├── graph.py
├── io.py
├── links.py
├── model_roadway.py
├── network.py
├── nodes.py
├── projects
│   ├── __init__.py
│   ├── add.py
│   ├── add_managed.py
│   ├── calculate.py
│   ├── delete.py
│   └── edit_property.py
├── segment.py
├── selection.py
├── shapes.py
├── subnet.py
├── utils.py
└── viz.py

2 directories, 21 files


In [77]:
!tree ../network_wrangler/transit -L 2 -I '.*|*.pyc|__pycache__'

../network_wrangler/transit
├── __init__.py
├── clip.py
├── convert.py
├── feed.py
├── geo.py
├── io.py
├── model_transit.py
├── network.py
├── projects
│   ├── __init__.py
│   ├── calculate.py
│   ├── edit_property.py
│   └── edit_routing.py
└── selection.py

2 directories, 13 files


## Smoother Installation

### Conda environments

`/environments/conda/environment.yml` contains a working conda environment which can be set up using:

```sh
conda env create -f environment.yml
```

### Installing from pip

GitHub Action will publish to PyPI automatically on each release and pre-release so you can install as follows:

```sh
pip install network_wrangler
```